# Stock Clustering

In this module of the financial web app, I will be performing an unsupervised clustering of data on a number of well-known stocks stored in the financial database created. Stocks are clustered on the basis of historical OHLCV data(daily returns) and Technical Inidicators(RSI, MACD etc.), this allows for grouping of stocks based on their behavioural patterns(how they tend to move with time) in the market.

We’re capturing things like:

📈 Trend behavior: Are they in an uptrend or downtrend?

🔁 Momentum: Do they accelerate upward/downward suddenly?

🔄 Mean-reversion vs. breakout: Do they bounce around a mean (like value stocks), or break out like growth stocks?

📊 Volatility dynamics: Do they swing hard or stay tight in range?

📦 Volume reactions: Does volume spike on price moves, or is it steady?



## Libraries

In [23]:
import warnings
warnings.simplefilter(action='ignore',category=FutureWarning)

import numpy as np
import pandas as pd
pd.set_option('display.max_columns',None)

# Data Visualisation
import matplotlib.pyplot as plt
%config InlineBackend.figure_format = 'retina'

import seaborn as sns
sns.set_style('darkgrid')

## Parameters and Variables

Setting some default parameters and variables for our whole notebook

In [24]:
font_size = 20
plt.rcParams['axes.labelsize'] = font_size
plt.rcParams['axes.titlesize'] = font_size + 2
plt.rcParams['xtick.labelsize'] = font_size - 2
plt.rcParams['ytick.labelsize'] = font_size - 2
plt.rcParams['legend.fontsize'] = font_size - 2

## Getting the Data

Here's a brief description of the data used here:

| Field      | Description                                         |
| ---------- | --------------------------------------------------- |
| **O**pen   | Price at the beginning of the trading period        |
| **H**igh   | Highest price during the period                     |
| **L**ow    | Lowest price during the period                      |
| **C**lose  | Price at the end of the period                      |
| **V**olume | Number of shares/contracts traded during the period |





| Indicator    | Type               | Measures                     | Use Case                           |
| ------------ | ------------------ | ---------------------------- | ---------------------------------- |
| **RSI**      | Momentum           | Overbought/Oversold          | Entry/exit signals                 |
| **MACD**     | Momentum           | Trend direction & strength   | Bullish/bearish signals            |
| **SMA**      | Trend              | Average price (equal weight) | Trend detection                    |
| **EMA**      | Trend              | Average price (recent bias)  | Faster trend signals               |
| **ATR**      | Volatility         | Magnitude of price movement  | Risk measurement                   |
| **BB Bands** | Volatility + Trend | Price position & squeeze     | Mean-reversion or breakout signals |










In [25]:
# Importing the libraries to get the data from the database
from sqlalchemy import create_engine
import pandas as pd
import os
from dotenv import load_dotenv

# Loading the DB credentials from .env file
load_dotenv()

# Getting the database details and storing it
def get_db_url():
    user = os.getenv("DB_USER")
    password = os.getenv("DB_PASSWORD")
    host = os.getenv("DB_HOST")
    port = os.getenv("DB_PORT","5432")
    db = os.getenv("DB_NAME")
    return f"postgresql://{user}:{password}@{host}:{port}/{db}"



In [26]:
# Loading the data from the database
def load_data(join: bool = False, chunksize: int = None, columns: list = None, limit:int = None):
    engine = create_engine(get_db_url())

    # Building the SELECT clause
    cols = ", ".join(columns) if columns else "*"

    # Defining the query with optional join
    if join:
        query = f"""
        SELECT {cols}
        FROM stock_data sd
        JOIN technical_indicators ti
        ON sd.ticker = ti.ticker and sd.date = ti.date"""

    else:
        query = f"SELECT {cols} FROM stock_data"

    if limit:
        query += f" LIMIT {limit}"

    if chunksize:
        return pd.read_sql(query, engine, chunksize=chunksize)
    else:
        df = pd.read_sql(query,engine)
        engine.dispose()
        return df


In [27]:
# Specifying the columns to be imported
columns = [
    "sd.ticker","sd.date","sd.open","sd.high","sd.low","sd.close","sd.volume",
    "ti.ticker","ti.date","ti.rsi","ti.macd","ti.sma","ti.ema","ti.atr","ti.bb_upper","ti.bb_middle","ti.bb_lower"

]

# Getting the data in batches
data_chunks = load_data(join=True,columns=columns,chunksize=10000)

In [28]:
# Loading the chunks to view them
for chunk in data_chunks:
    print(chunk.head())

  ticker        date    open    high     low   close    volume ticker  \
0   AAPL  2025-05-20  207.67  208.47  205.03  206.86  40940792   AAPL   
1   AAPL  2025-05-19  207.91  209.48  204.26  208.78  46140500   AAPL   
2   AAPL  2025-05-16  212.36  212.57  209.77  211.26  54737900   AAPL   
3   AAPL  2025-05-15  210.95  212.96  209.54  211.45  45029500   AAPL   
4   AAPL  2025-02-10  229.57  230.59  227.20  227.65  33115600   AAPL   

         date      rsi    macd       sma       ema     atr  bb_upper  \
0  2025-05-20  50.9125  0.6616  207.9322  208.2333  6.3560  218.3768   
1  2025-05-19  51.9873  0.6951  206.6456  208.3341  6.6680  218.3950   
2  2025-05-16  54.7913  0.6309  205.5044  208.2227  6.6425  218.9238   
3  2025-05-15  55.0024  0.2873  204.1300  207.4634  6.9380  218.4958   
4  2025-02-10  41.6908 -2.5951  232.7478  230.9541  6.0456  241.4600   

   bb_middle  bb_lower  
0   206.9875  195.5982  
1   206.5860  194.7770  
2   205.8050  192.6862  
3   205.0910  191.6862  
4  

In [29]:
# Loading all the chunks into a single dataframe
full_df = pd.concat(load_data(join=True,chunksize=10000,columns=columns),ignore_index=True)
full_df.head()

ticker        date    open    high     low   close    volume ticker  \
0   AAPL  2025-05-20  207.67  208.47  205.03  206.86  40940792   AAPL   
1   AAPL  2025-05-19  207.91  209.48  204.26  208.78  46140500   AAPL   
2   AAPL  2025-05-16  212.36  212.57  209.77  211.26  54737900   AAPL   
3   AAPL  2025-05-15  210.95  212.96  209.54  211.45  45029500   AAPL   
4   AAPL  2025-02-10  229.57  230.59  227.20  227.65  33115600   AAPL   

         date      rsi    macd       sma       ema     atr  bb_upper  \
0  2025-05-20  50.9125  0.6616  207.9322  208.2333  6.3560  218.3768   
1  2025-05-19  51.9873  0.6951  206.6456  208.3341  6.6680  218.3950   
2  2025-05-16  54.7913  0.6309  205.5044  208.2227  6.6425  218.9238   
3  2025-05-15  55.0024  0.2873  204.1300  207.4634  6.9380  218.4958   
4  2025-02-10  41.6908 -2.5951  232.7478  230.9541  6.0456  241.4600   

   bb_middle  bb_lower  
0   206.9875  195.5982  
1   206.5860  194.7770  
2   205.8050  192.6862  
3   205.0910  191.6862  
4   230.9775  220.4950

In [30]:
# Getting the number of datapoints
print("The number of rows is {} and the number of columns is {}".format(full_df.shape[0],full_df.shape[1]))


The number of rows is 11940 and the number of columns is 17


## Data Cleaning

In this section:

* Data Cleaning
* Feature Engineering

In [31]:
# Getting info on the dataset, to define the cleaning method

full_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11940 entries, 0 to 11939
Data columns (total 17 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   ticker     11940 non-null  object 
 1   date       11940 non-null  object 
 2   open       11940 non-null  float64
 3   high       11940 non-null  float64
 4   low        11940 non-null  float64
 5   close      11940 non-null  float64
 6   volume     11940 non-null  int64  
 7   ticker     11940 non-null  object 
 8   date       11940 non-null  object 
 9   rsi        11940 non-null  float64
 10  macd       11940 non-null  float64
 11  sma        11940 non-null  float64
 12  ema        11940 non-null  float64
 13  atr        11940 non-null  float64
 14  bb_upper   11940 non-null  float64
 15  bb_middle  11940 non-null  float64
 16  bb_lower   11940 non-null  float64
dtypes: float64(12), int64(1), object(4)
memory usage: 1.5+ MB


**From the above output, we can conclude that:**

* There are no missing values whatsoever
* There are duplicate columns for ticker and data which will be removed
* date is stored as an object not datetime, this will be converted
* ticker is categorical and will be encoded into numerical forms later

In [32]:
# Dropping the duplicate columns
full_df = full_df.loc[:,~full_df.columns.duplicated()]
full_df.head()

ticker        date    open    high     low   close    volume      rsi  \
0   AAPL  2025-05-20  207.67  208.47  205.03  206.86  40940792  50.9125   
1   AAPL  2025-05-19  207.91  209.48  204.26  208.78  46140500  51.9873   
2   AAPL  2025-05-16  212.36  212.57  209.77  211.26  54737900  54.7913   
3   AAPL  2025-05-15  210.95  212.96  209.54  211.45  45029500  55.0024   
4   AAPL  2025-02-10  229.57  230.59  227.20  227.65  33115600  41.6908   

     macd       sma       ema     atr  bb_upper  bb_middle  bb_lower  
0  0.6616  207.9322  208.2333  6.3560  218.3768   206.9875  195.5982  
1  0.6951  206.6456  208.3341  6.6680  218.3950   206.5860  194.7770  
2  0.6309  205.5044  208.2227  6.6425  218.9238   205.8050  192.6862  
3  0.2873  204.1300  207.4634  6.9380  218.4958   205.0910  191.6862  
4 -2.5951  232.7478  230.9541  6.0456  241.4600   230.9775  220.4950

### Feature Engineering

Now, we will engineer new features, that will help us in the model training, as it will help the model to better understand patterns



In [33]:
# First of all, we will convert date to datetime
full_df['date'] = pd.to_datetime(full_df['date'])

# Sorting by ticker and date
full_df = full_df.sort_values(by=['ticker','date'])

#### Daily Return

In [34]:
full_df['daily_return'] = full_df.groupby('ticker')['close'].pct_change()

#Grouping now
grouped = full_df.groupby('ticker')

#### Rolling Volatility

In [35]:
full_df['rolling_volatility'] = grouped['daily_return'].rolling(window=3).std().reset_index(level=0, drop=True)

#### Average Volume

In [36]:
full_df['avg_volume'] = grouped['volume'].rolling(window=3).mean().reset_index(level=0, drop=True)


#### Trend Strength

In [37]:
full_df['trend_strength'] = (full_df['close'] - full_df['sma'])/full_df['sma']

#### Volatility Range

In [38]:
full_df['volatility_range'] = full_df['high'] - full_df['low']

In [39]:
# Dropping rows from rolling operations
full_df = full_df.dropna().reset_index(drop=True)

In [40]:
full_df.head()

ticker       date    open    high     low   close    volume      rsi  \
0   AAPL 2023-01-06  126.01  130.29  124.89  129.62  87754700  42.1189   
1   AAPL 2023-01-09  130.47  133.41  129.89  130.15  70790800  43.0379   
2   AAPL 2023-01-10  130.26  131.26  128.12  130.73  63896200  44.0842   
3   AAPL 2023-01-11  131.25  133.51  130.46  133.49  69458900  48.8949   
4   AAPL 2023-01-12  133.88  134.26  131.44  133.41  71379600  48.7639   

     macd       sma       ema     atr  bb_upper  bb_middle  bb_lower  \
0 -4.5841  128.1711  128.8381  4.3780  146.7155   133.7440  120.7725   
1 -4.2292  127.9811  129.1005  4.3360  145.5051   133.1190  120.7329   
2 -3.8566  128.0589  129.4264  4.2505  144.2481   132.5475  120.8469   
3 -3.3006  128.8867  130.2391  4.1648  142.3583   131.9975  121.6367   
4 -2.8338  129.3089  130.8733  4.0687  139.7605   131.3945  123.0285   

   daily_return  rolling_volatility    avg_volume  trend_strength  \
0      0.036794            0.023754  8.594367e+07        0.011304   
1      0.004089            0.024263  7.983607e+07        0.016947   
2      0.004456            0.018777  7.414723e+07        0.020858   
3      0.021112            0.009724  6.804863e+07        0.035716   
4     -0.000599            0.011361  6.824490e+07        0.031716   

   volatility_range  
0              5.40  
1              3.52  
2              3.14  
3              3.05  
4              2.82

In [41]:
# Now, that we have some new features, lets look at the data stats
full_df.describe()

date          open          high  \
count                          11880  11880.000000  11880.000000   
mean   2024-03-13 10:15:45.454545664    188.063909    190.043886   
min              2023-01-06 00:00:00     14.470000     15.010000   
25%              2023-08-10 00:00:00     94.505000     95.685000   
50%              2024-03-13 12:00:00    160.045000    161.345000   
75%              2024-10-15 00:00:00    245.162500    248.690000   
max              2025-05-20 00:00:00    736.000000    740.910000   
std                              NaN    131.736633    133.132926   

                low         close        volume           rsi          macd  \
count  11880.000000  11880.000000  1.188000e+04  11880.000000  11880.000000   
mean     186.117587    188.171947  4.413244e+07     52.928694      0.930545   
min       14.030000     14.860000  9.550000e+05     14.075200    -35.583200   
25%       93.507500     94.752500  7.017100e+06     43.901650     -0.834975   
50%      158.880000    160.260000  1.563340e+07     53.268200      0.454450   
75%      242.222500    245.715000  3.692430e+07     62.204675      2.454300   
max      725.620000    736.670000  1.543911e+09     89.064400     40.538600   
std      130.295936    131.774723  9.517598e+07     12.603924      4.681909   

                sma           ema           atr      bb_upper     bb_middle  \
count  11880.000000  11880.000000  11880.000000  11880.000000  11880.000000   
mean     187.518160    187.539959      4.262106    197.105121    186.724286   
min       14.529800     14.801300      0.460700     17.379600     15.470900   
25%       94.231650     94.141000      1.883200    100.239600     93.598000   
50%      160.332800    160.327700      3.007300    166.329050    159.830000   
75%      244.968325    244.567725      5.901075    262.026250    242.412125   
max      719.506700    716.377500     34.560900    760.723900    700.719000   
std      131.146865    131.121833      3.910643    138.054453    130.409854   

           bb_lower  daily_return  rolling_volatility    avg_volume  \
count  11880.000000  11880.000000        11880.000000  1.188000e+04   
mean     176.343458      0.001004            0.013843  4.416425e+07   
min       12.704100     -0.169682            0.000017  1.202133e+06   
25%       87.657925     -0.007426            0.006269  7.212483e+06   
50%      152.770850      0.000819            0.010471  1.599908e+07   
75%      225.532000      0.008943            0.017231  3.723962e+07   
max      659.261200      0.243615            0.166566  1.060570e+09   
std      123.328837      0.018724            0.012689  9.307580e+07   

       trend_strength  volatility_range  
count    11880.000000      11880.000000  
mean         0.003441          3.926299  
min         -0.183869          0.180000  
25%         -0.011775          1.390000  
50%          0.003435          2.640000  
75%          0.017553          4.970000  
max          0.256322         85.780000  
std          0.029138          4.255291

## Interactive Plots

### **CandleStick Chart**

We will now visualise the price and indicator trends of all the stocks(behaviour over time)

In [42]:
import plotly.graph_objects as go

#Ensuring that date is a datetime object
full_df['date'] = pd.to_datetime(full_df['date'])

# Getting the list of unique tickers
tickers = full_df['ticker'].unique()

#Creating a figure object
fig = go.Figure()

# Creating one trace group per ticker (each will be shown/hidden via dropdown)
for ticker in tickers:
    df_t = full_df[full_df['ticker'] == ticker].sort_values('date')

    # Candlestick
    fig.add_trace(go.Candlestick(
        x=df_t['date'],
        open = df_t['open'],
        high = df_t['high'],
        low = df_t['low'],
        close = df_t['close'],
        name = f'{ticker} OHLC',
        visible = (ticker == tickers[0]) # Show only the first by default
    ))

    #SMA
    fig.add_trace(go.Scatter(
        x = df_t['date'],
        y = df_t['sma'],
        name = f'{ticker} SMA',
        line = dict(color='blue'),
        visible = (ticker == tickers[0])
    ))

    #EMA
    fig.add_trace(go.Scatter(
        x = df_t['date'],
        y = df_t['ema'],
        name = f'{ticker} EMA',
        line = dict(color='orange'),
        visible = (ticker == tickers[0])
    ))

    # Bollinger Upper
    fig.add_trace(go.Scatter(
        x = df_t['date'],
        y = df_t['bb_upper'],
        name = f'{ticker} BB Upper',
        line = dict(color = 'gray',dash = 'dot'),
        visible = (ticker == tickers[0])
    ))

    # Bollinger Lower
    fig.add_trace(go.Scatter(
        x = df_t['date'],
        y = df_t['bb_lower'],
        name = f'{ticker} BB Lower',
        line = dict(color = 'gray',dash = 'dot'),
        visible = (ticker == tickers[0]),
        fill = 'tonexty',
        fillcolor = 'rgba(173,216,230,0.2)'
    ))

# Creating dropdown buttons to toggle ticker traces
dropdown_buttons = []
traces_per_ticker = 5

for i,ticker in enumerate(tickers):
    visibility = [False] * traces_per_ticker * len(tickers)
    for j in range(traces_per_ticker):
        visibility[i * traces_per_ticker + j] = True

    dropdown_buttons.append(dict(
        label = ticker,
        method = "update",
        args = [{"visible":visibility},
                {"title": f"{ticker} Candlestick chart with Indicators"}]

    ))


#Update layout with dropdown
fig.update_layout(
    title = f"{tickers[0]} Candlestick chart with Indicators",
    xaxis_title = "Date",
    yaxis_title = "Price",
    xaxis_rangeslider_visible = False,
    template = "plotly_dark",
    hovermode = "x unified",
    updatemenus = [{
        "buttons": dropdown_buttons,
        "direction": "down",
        "showactive": True,
        "x": 0.0,
        "xanchor": "left",
        "y": 1.1,
        "yanchor": "top"
    }]
)

fig.show()



### **MACD/RSI Timeline**

We can now select a stock and see its momentum over time and identify entry/exit signals:

RSI > 70: Potentially overbought

RSI < 30: Potentially oversold

MACD crossing above 0: Bullish trend

MACD crossing below 0: Bearish trend

In [47]:
import plotly.graph_objects as go

# Just making sure date is a datetime object
full_df['date'] = pd.to_datetime(full_df['date'])

#List of unique tickers
tickers = full_df['ticker'].unique()

# Creating a figure with initial stock (first ticker)
init_ticker = tickers[0]
init_df = full_df[full_df['ticker'] == init_ticker]

#Create subplots: RSI (top) + MACD (bottom)
from plotly.subplots import make_subplots

fig = make_subplots(rows=2, cols=1, shared_xaxes=True,
                    vertical_spacing=0.1,
                    subplot_titles=("RSI Timeline","MACD Timeline"))


# RSI Plot
fig.add_trace(go.Scatter(
    x = init_df['date'],
    y = init_df['rsi'],
    mode = 'lines',
    name = 'RSI',
    line = dict(color='royalblue')
), row=1,col=1)

# MACD Plot
fig.add_trace(go.Scatter(
    x = init_df['date'],
    y = init_df['macd'],
    mode = 'lines',
    name = 'MACD',
    line = dict(color='purple')

), row=2,col=1)

# Adding dropdown menu for interactivity
dropdown_buttons = []

for ticker in tickers:
    ticker_df = full_df[full_df['ticker'] == ticker]
    dropdown_buttons.append(dict(
        label = ticker,
        method = 'update',
        args = [{
            'y': [ticker_df['rsi'],ticker_df['macd']],
            'x': [ticker_df['date'], ticker_df['date']]
        }]
    ))

fig.update_layout(
    updatemenus = [dict(
        buttons = dropdown_buttons,
        direction = 'down',
        showactive = True,
        x = 1.15,
        y = 1.15

    )],
    height = 600,
    title_text = 'MACD and RSI Timeline',
    template = 'plotly_dark'
)

# Adding RSI reference lines
fig.add_shape(type='line', x0=init_df['date'].min(),x1=init_df['date'].max(),
              y0=70,y1=70, line=dict(dash='dash', color='gray'), row=1,col=1)
fig.add_shape(type='line', x0=init_df['date'].min(), x1=init_df['date'].max(),
              y0=30, y1=30, line=dict(dash='dash', color='gray'), row=1, col=1)

fig.show()